In [1]:
import datetime as dt

import matplotlib.pyplot as plt
import mplfinance as mpf
import numpy as np
import pandas as pd
import pandas_market_calendars as mcal
import plotly.graph_objects as go
import polars as pl
from dash import Dash, dcc, html
from plotly.subplots import make_subplots

nse = mcal.get_calendar("NSE")

pd.set_option("display.max_rows", 25_000)
pd.set_option("display.max_columns", 500)
pl.Config.set_tbl_cols(500)
pl.Config.set_tbl_rows(10_000)

pd.options.display.float_format = "{:.4f}".format

import sys

sys.path.append("..")
from tooling.enums import AssetClass, Index, Spot, StrikeSpread
from tooling.fetch import fetch_option_data, fetch_spot_data
from tooling.filter import find_atm, option_tool

from fetching_from_local_db.enums import AssetClass, Index, StrikeSpread
from fetching_from_local_db.fetch_from_db import _fetch_batch, fetch_data, fetch_spot_data

In [2]:
async def get_expiry(f_today):

    if (f_today <= dt.date(2024, 1, 25)) and (f_today >= dt.date(2024, 1, 18)):
        f_expiry = dt.date(2024, 1, 25)
    elif (f_today <= dt.date(2024, 1, 31)) and (f_today >= dt.date(2024, 1, 26)):
        f_expiry = dt.date(2024, 1, 31)
    elif (f_today <= dt.date(2024, 2, 22)) and (f_today >= dt.date(2024, 2, 29)):
        f_expiry = dt.date(2024, 2, 29)
    elif (f_today <= dt.date(2024, 3, 25)) and (f_today >= dt.date(2024, 3, 27)):
        f_expiry = dt.date(2024, 2, 27)
    elif f_today < dt.date(2023, 9, 1):
        days_to_thursday = (3 - f_today.weekday()) % 7
        nearest_thursday = f_today + dt.timedelta(days=days_to_thursday)
        f_expiry = nearest_thursday
        if nse.valid_days(start_date=nearest_thursday, end_date=nearest_thursday).empty:
            f_expiry = nearest_thursday - dt.timedelta(days=1)
    elif f_today >= dt.date(2023, 9, 1):
        if f_today.day < 24:
            days_to_wednesday = (2 - f_today.weekday()) % 7
            nearest_wednesday = f_today + dt.timedelta(days=days_to_wednesday)
            f_expiry = nearest_wednesday
            if nse.valid_days(
                start_date=nearest_wednesday, end_date=nearest_wednesday
            ).empty:
                f_expiry = nearest_wednesday - dt.timedelta(days=1)
        else:
            days_to_thursday = (3 - f_today.weekday()) % 7
            nearest_thursday = f_today + dt.timedelta(days=days_to_thursday)
            f_expiry = nearest_thursday
            if nse.valid_days(
                start_date=nearest_thursday, end_date=nearest_thursday
            ).empty:
                f_expiry = nearest_thursday - dt.timedelta(days=1)
    return f_expiry


async def get_expiry_finnifty(f_today):

    days_to_thursday = (1 - f_today.weekday()) % 7
    nearest_thursday = f_today + dt.timedelta(days=days_to_thursday)
    f_expiry = nearest_thursday
    if nse.valid_days(start_date=nearest_thursday, end_date=nearest_thursday).empty:
        f_expiry = nearest_thursday - dt.timedelta(days=1)
    return f_expiry

async def get_expiry_nifty(f_today):

    days_to_thursday = (3 - f_today.weekday()) % 7
    nearest_thursday = f_today + dt.timedelta(days=days_to_thursday)
    f_expiry = nearest_thursday
    if nse.valid_days(start_date=nearest_thursday, end_date=nearest_thursday).empty:
        f_expiry = nearest_thursday - dt.timedelta(days=1)
    return f_expiry

async def get_expiry_midcpnifty(f_today):

    days_to_thursday = (0 - f_today.weekday()) % 7
    nearest_thursday = f_today + dt.timedelta(days=days_to_thursday)
    f_expiry = nearest_thursday
    if nse.valid_days(start_date=nearest_thursday, end_date=nearest_thursday).empty:
        f_expiry = nearest_thursday - dt.timedelta(days=1)
    return f_expiry


async def get_option_contract_name(symbol, strike, expiry, opt_type):
    temp = "0"
    mth = expiry.month

    if (expiry + dt.timedelta(days=7)).month != expiry.month:
        date_string = expiry.strftime("%y%b").upper()
        return f"{symbol}{date_string}{strike}{opt_type}"
    else:
        if expiry.day <= 9:
            date_string = f"{expiry.year - 2000}{mth}{temp}{expiry.day}"
        else:
            date_string = f"{expiry.year - 2000}{mth}{expiry.day}"
        return f"{symbol}{date_string}{strike}{opt_type}"

In [3]:
# bnf_pandas = pd.read_csv("../data/bnf_1hr_tv (7).csv")
bnf_pandas = pd.read_csv("../data/fin.csv")
# bnf_pandas = bnf_pandas[bnf_pandas['datetime'].dt.year >= 2023]
# bnf_pandas = pd.read_csv('../data/midcp_select_1hr_tv (4).csv')
# bnf_pandas = pd.read_csv('../data/sensex_1hr_tv.csv')
# bnf_pandas = pd.read_csv('../data/crude_4hr_tv.csv')
# bnf_pandas = pd.read_csv('../data/gold_4hr_tv.csv')

In [4]:
# If Stocks Data ...
bnf_pandas["datetime"] = pd.to_datetime(bnf_pandas["datetime"])
bnf_pandas["datetime"] = bnf_pandas["datetime"].dt.tz_localize(None)
bnf_pandas = bnf_pandas[bnf_pandas["datetime"].dt.year >= 2017]
# bnf_pandas.drop(columns=["time"], inplace=True)
# bnf_pandas

In [5]:
bnf = pl.DataFrame(bnf_pandas)
print(type(bnf))
# bnf

<class 'polars.dataframe.frame.DataFrame'>


In [6]:
bnf = bnf.with_columns([pl.col("datetime").alias("index")]).drop("datetime")
bnf = bnf.with_columns(pl.col("index").alias("datetime"))
bnf.head()

shape: (5, 7)
┌─────────┬─────────┬─────────┬─────────┬────────┬─────────────────────┬─────────────────────┐
│ open    ┆ high    ┆ low     ┆ close   ┆ volume ┆ index               ┆ datetime            │
│ ---     ┆ ---     ┆ ---     ┆ ---     ┆ ---    ┆ ---                 ┆ ---                 │
│ f64     ┆ f64     ┆ f64     ┆ f64     ┆ i64    ┆ datetime[ns]        ┆ datetime[ns]        │
╞═════════╪═════════╪═════════╪═════════╪════════╪═════════════════════╪═════════════════════╡
│ 7442.4  ┆ 7442.4  ┆ 7398.05 ┆ 7399.3  ┆ 0      ┆ 2017-01-02 09:15:00 ┆ 2017-01-02 09:15:00 │
│ 7399.7  ┆ 7411.95 ┆ 7399.7  ┆ 7407.5  ┆ 0      ┆ 2017-01-02 09:16:00 ┆ 2017-01-02 09:16:00 │
│ 7407.7  ┆ 7408.95 ┆ 7385.75 ┆ 7385.75 ┆ 0      ┆ 2017-01-02 09:17:00 ┆ 2017-01-02 09:17:00 │
│ 7386.05 ┆ 7389.9  ┆ 7382.4  ┆ 7388.9  ┆ 0      ┆ 2017-01-02 09:18:00 ┆ 2017-01-02 09:18:00 │
│ 7389.45 ┆ 7389.9  ┆ 7382.05 ┆ 7384.05 ┆ 0      ┆ 2017-01-02 09:19:00 ┆ 2017-01-02 09:19:00 │
└─────────┴─────────┴─────────┴─────────┴────────┴─────────────────────┴─────────────────────┘

In [7]:
def resample(
    data: pl.DataFrame, timeframe, offset: dt.timedelta | None = None
) -> pl.DataFrame:
    return (
        data.set_sorted("datetime")
        .group_by_dynamic(
            index_column="datetime",
            every=timeframe,
            period=timeframe,
            label="left",
            offset=offset,
        )
        .agg(
            [
                pl.col("o").first().alias("o"),
                pl.col("h").max().alias("h"),
                pl.col("l").min().alias("l"),
                pl.col("c").last().alias("c"),
                # pl.col("volume").sum().alias("volume"),
            ]
        )
    )


# ohlc_resampled = resample(bnf, '5m', pd.Timedelta(minutes=0))

# bnf_1hr = ohlc_resampled
# bnf_final = bnf_1hr.to_pandas()
# bnf_final['datetime'] = pd.to_datetime(bnf_final['datetime'])
# bnf_final
# bnf_1hr

In [8]:
def generate_signals2(df, signal_ma, trailing_ma):
    df["c"] = pd.to_numeric(df["c"], errors="coerce")
    df["MA20"] = df["c"].rolling(window=signal_ma).mean()
    df["MA10"] = df["c"].rolling(window=trailing_ma).mean()

    df["Sell_Signal"] = 0

    # Generate signals using boolean masking
    sell_signal_mask = ((
        df["MA20"]
        < df["MA20"].shift(1))
        & (df["MA20"].shift(1) < df["MA20"].shift(2))
        & (df["MA20"].shift(2) < df["MA20"].shift(3))
        & (df["MA20"].shift(3) < df["MA20"].shift(4))
        # & (df["MA20"].shift(4) < df["MA20"].shift(5))
        # & (df['MA20'].shift(5) < df['MA20'].shift(6))
        # & (df['MA20'].shift(6) < df['MA20'].shift(7))
    )

    df.loc[sell_signal_mask, "Sell_Signal"] = 1

    return df

In [9]:
data = bnf_pandas.copy()
# data['datetime'] = pd.to_datetime(data['datetime'].dt.date)
print(data["datetime"].tail())
trading_days_set = set(data["datetime"].dt.date)
# sorted(trading_days_set)

869531   2024-06-07 15:25:00
869532   2024-06-07 15:26:00
869533   2024-06-07 15:27:00
869534   2024-06-07 15:28:00
869535   2024-06-07 15:29:00
Name: datetime, dtype: datetime64[ns]


In [10]:
# GLOBAL VARIABLES

# INSTRUMENT = "BANKNIFTY"
# INDEX = "bnf"

# INSTRUMENT = "MIDCPNIFTY"
# INDEX = "midcpnifty"

INSTRUMENT = "FINNIFTY"
INDEX = "finnifty"

PORTFOLIO_VALUE = 25_00_000
INDEX_LEV = 6

In [11]:
data

datetime       open       high        low      close  volume
181911 2017-01-02 09:15:00  7442.4000  7442.4000  7398.0500  7399.3000       0
181912 2017-01-02 09:16:00  7399.7000  7411.9500  7399.7000  7407.5000       0
181913 2017-01-02 09:17:00  7407.7000  7408.9500  7385.7500  7385.7500       0
181914 2017-01-02 09:18:00  7386.0500  7389.9000  7382.4000  7388.9000       0
181915 2017-01-02 09:19:00  7389.4500  7389.9000  7382.0500  7384.0500       0
...                    ...        ...        ...        ...        ...     ...
869531 2024-06-07 15:25:00 22162.5000 22166.0500 22157.2500 22163.7000       0
869532 2024-06-07 15:26:00 22163.8000 22165.4000 22158.3500 22163.5000       0
869533 2024-06-07 15:27:00 22165.2500 22172.2000 22160.2000 22169.1500       0
869534 2024-06-07 15:28:00 22169.8500 22171.9500 22164.6500 22168.3000       0
869535 2024-06-07 15:29:00 22170.6000 22171.9000 22162.0000 22166.8000       0

[687625 rows x 6 columns]

In [12]:
async def trade_mtrend_option_selling(
    df, index, strike, asset_class, expiry, search_datetime
):

    trade_book = []
    in_trade = False
    signal_entry_price = 100000
    signal_initial_sl = 0
    already_signal_exists = False
    is_trailing_active = False
    eod_exit_flag = False
    remark = ""

    for i in range(0, len(df)):
        subset_df = df[:i+1]
        if df.iloc[i]['datetime'] >= search_datetime and df.iloc[i]['datetime'].time() <= dt.time(15, 20):
            # print(df.iloc[i]['datetime'])
            points = 0
            current_candle_open = df.iloc[i]["o"]
            current_candle_high = df.iloc[i]["h"]
            current_candle_low = df.iloc[i]["l"]
            current_candle_close = df.iloc[i]["c"]
            current_moving_average_price = df.iloc[i]["MA10"]
    
            if not in_trade:
                if df.iloc[i]["Sell_Signal"] == 1:
                    if not already_signal_exists:
                        # Fresh Sell Signal
    
                        # print(df.iloc[i])
                        # print('Fresh Sell Signal')                        
                        signal_entry_price = current_candle_low
                        # signal_initial_sl = current_candle_high
                        # signal_initial_sl = max(current_candle_high, df.iloc[i-1]['h'], df.iloc[i-2]['h'], df.iloc[i-3]['h'], df.iloc[i-4]['h'])
                        signal_initial_sl = subset_df['h'].max()
                        signal_target = 0 * signal_entry_price
                        signal_creation_time = df.iloc[i]["datetime"]
                        already_signal_exists = True
                        # print(signal_entry_price, signal_initial_sl)
    
                        # if (signal_entry_price - signal_initial_sl > 400):
                        #     # Skip Signal Candle Due To Big Size
    
                        #     already_signal_exists = False
                        #     signal_entry_price = 100000
                        #     signal_initial_sl = 0
    
                    else:
                        # if current_candle_open < signal_entry_price:
                        #     # Gap Up Open, SKIP trade
    
                        #     # print(df.iloc[i])
                        #     # print('Gap Up Open, Skip Trade')
                        #     already_signal_exists = False
                        #     signal_entry_price = 100000
                        #     signal_initial_sl = 0
    
                        if current_candle_low > signal_entry_price:
                            # Better Candle
    
                            # print(df.iloc[i])
                            # print('Better Candle')
                            
                            signal_entry_price = current_candle_low
                            # signal_initial_sl = current_candle_high
                            # signal_initial_sl = max(current_candle_high, df.iloc[i-1]['h'], df.iloc[i-2]['h'], df.iloc[i-3]['h'], df.iloc[i-4]['h'])
                            signal_initial_sl = subset_df['h'].max()
                            signal_creation_time = df.iloc[i]["datetime"]
                            # print(signal_entry_price, signal_initial_sl)
    
                            # if (signal_entry_price - signal_initial_sl > 400):
                            #     # Skip Signal Candle Due To Big Size
    
                            #     already_signal_exists = False
                            #     signal_entry_price = 100000
                            #     signal_initial_sl = 0
    
                        elif current_candle_low <= signal_entry_price:
                            # Entry Triggered
    
                            # print(df.iloc[i])
                            # print('Entry Triggered')
                            in_trade = True
                            entry_time = df.iloc[i]["datetime"]
                            entry_price = signal_entry_price
                            # print(entry_price, signal_initial_sl)
                            points = 0
    
                else:
                    if (df.iloc[i - 1]["Sell_Signal"] == 1):
                        # Considering the forward bias condition as well now
                        # print('Forward Bias Avoided Condition Triggered')
                        signal_entry_price = df.iloc[i - 1]["l"]
                        # signal_initial_sl = df.iloc[i-1]['h']
                        # signal_initial_sl = max(df.iloc[i-1]['h'], df.iloc[i-2]['h'], df.iloc[i-3]['h'], df.iloc[i-4]['h'], df.iloc[i-5]['h'])
                        signal_initial_sl = subset_df['h'].max()
                        signal_target = 0 * signal_entry_price
                        signal_creation_time = df.iloc[i - 1]["datetime"]
                        already_signal_exists = True
                        
                        # print(signal_entry_price, signal_initial_sl)
                        # print(subset_df.to_string())
    
                        if current_candle_low <= signal_entry_price:
                            in_trade = True
                            entry_time = df.iloc[i]["datetime"]
                            entry_price = signal_entry_price
                            points = 0
                            # print(entry_price, signal_initial_sl)
                        else:
                            # Discard Existing Signal
                            already_signal_exists = False
                            signal_entry_price = 100000
                            signal_initial_sl = 0

            if in_trade:
                trade_entry_price = signal_entry_price
                trade_initial_sl = signal_initial_sl
                trade_final_sl = signal_initial_sl
                trade_target = signal_target
    
                if (
                    not is_trailing_active
                    and current_candle_high < current_moving_average_price
                ):
                    is_trailing_active = False
    
                if not is_trailing_active:
                    if current_candle_open > trade_initial_sl:
                        # if df.iloc[i-1]['l'] < trade_initial_sl:
                        #     #Previous Candle Already Hit the SL Hence don't check gap down
                        #     print(df.iloc[i])
                        #     print('Initial SL Hit Before Gap Down')
                        #     in_trade = False
                        #     points = trade_initial_sl - trade_entry_price
                        #     exit_price = trade_initial_sl
                        #     exit_time = df.iloc[i-1]['datetime']
                        #     remark = 'Initial SL Hit Before Gap Down'
                        # else:
                        if (
                            df.iloc[i]["datetime"].date() == entry_time.date()
                            and df.iloc[i]["datetime"].time() == entry_time.time()
                        ):
                            if current_candle_close >= trade_initial_sl:
                                in_trade = False
                                points = -1 * (trade_initial_sl - trade_entry_price)
                                exit_price = trade_initial_sl
                                exit_time = df.iloc[i]["datetime"]
                                remark = "Initial SL hit"
    
                        else:
                            # Gap Open Outside ISL
    
                            # print(df.iloc[i])
                            # print('Gap Open Outside ISL')
                            in_trade = False
                            points = -1 * (current_candle_open - trade_entry_price)
                            exit_price = current_candle_open
                            exit_time = df.iloc[i]["datetime"]
                            remark = "Gap Open Outside ISL"
    
                    elif current_candle_high >= trade_initial_sl:
                        # Initial SL Hit
    
                        # print(df.iloc[i])
                        # print('Initial SL Hit')
                        # print(current_candle_high, trade_initial_sl)
                        in_trade = False
                        points = -1 * (trade_initial_sl - trade_entry_price)
                        exit_price = trade_initial_sl
                        exit_time = df.iloc[i]["datetime"]
                        remark = "Initial SL Hit"

                    elif current_candle_low <= trade_target:
                        # Target Hit
    
                        # print(df.iloc[i])
                        # print('Target Hit')
                        in_trade = False
                        points = -1 * (trade_target - trade_entry_price)
                        exit_price = trade_target
                        exit_time = df.iloc[i]["datetime"]
                        remark = "Target Hit"
    
                    elif df.iloc[i]["datetime"].time() >= dt.time(15, 20) and not eod_exit_flag:
                        # EOD Exit
    
                        # print(df.iloc[i])
                        # print('EOD Exit')
                        in_trade = False
                        points = -1 * (current_candle_close - trade_entry_price)
                        exit_price = current_candle_close
                        exit_time = df.iloc[i]["datetime"]
                        remark = "EOD Exit"
                        eod_exit_flag = True
    
                else:
                    trade_final_sl = min(trade_initial_sl, current_moving_average_price)
    
                    if current_candle_open >= trade_initial_sl:
                        # if df.iloc[i-1]['l'] < trade_initial_sl:
                        #     #Previous Candle Already Hit the SL Hence don't check gap down
                        #     print(df.iloc[i])
                        #     print('Initial SL Hit Before Gap Down')
                        #     in_trade = False
                        #     points = trade_initial_sl - trade_entry_price
                        #     exit_price = trade_initial_sl
                        #     exit_time = df.iloc[i-1]['datetime']
                        #     remark = 'Initial SL Hit'
                        # else:
                        if (
                            df.iloc[i]["datetime"].date() == entry_time.date()
                            and df.iloc[i]["datetime"].time() == entry_time.time()
                        ):
                            if current_candle_close >= trade_initial_sl:
                                in_trade = False
                                points = -1 * (trade_initial_sl - trade_entry_price)
                                exit_price = trade_initial_sl
                                exit_time = df.iloc[i]["datetime"]
                                remark = "Initial SL hit"
    
                        else:
                            # Gap Open Outside ISL
    
                            # print(df.iloc[i])
                            # print('Gap Open Outside ISL')
                            in_trade = False
                            points = trade_entry_price - current_candle_open
                            exit_price = current_candle_open
                            exit_time = df.iloc[i]["datetime"]
                            remark = "Gap Open Outside ISL"
    
                    elif current_candle_high >= trade_initial_sl:
                        # if trade_initial_sl >= current_moving_average_price:
    
                        # Despite Trailing, Initial SL hit
                        # print(df.iloc[i])
                        # print('Initial SL Hit')
                        in_trade = False
                        points = -1 * (trade_initial_sl - trade_entry_price)
                        exit_price = trade_initial_sl
                        exit_time = df.iloc[i]["datetime"]
                        remark = "Initial SL hit"

                    elif current_candle_low <= trade_target:
                        # Target Hit
    
                        # print(df.iloc[i])
                        # print('Target Hit')
                        in_trade = False
                        points = -1 * (trade_target - trade_entry_price)
                        exit_price = trade_target
                        exit_time = df.iloc[i]["datetime"]
                        remark = "Target Hit"
    
                    # elif current_candle_close >= trade_final_sl:
                    #     # Price Closed below TSL i.e. MA10 , TSL Hit
    
                    #     # print(df.iloc[i])
                    #     # print('Initial SL Hit')
                    #     in_trade = False
                    #     points = -1 * (current_candle_close - trade_entry_price)
                    #     exit_price = current_candle_close
                    #     exit_time = df.iloc[i]["datetime"]
                    #     is_trailing_active = False
                    #     remark = "TSL Hit"
    
                    elif df.iloc[i]["datetime"].time() >= dt.time(15, 20) and not eod_exit_flag:
                        # EOD Exit
    
                        # print(df.iloc[i])
                        # print('EOD Exit')
                        in_trade = False
                        points = trade_entry_price - current_candle_close
                        exit_price = current_candle_close
                        exit_time = df.iloc[i]["datetime"]
                        remark = "EOD Exit"
    
                if points:
                    
                    qty = int(round(PORTFOLIO_VALUE * INDEX_LEV / strike / 15)) * 15
                    slippage = 0.01 * (entry_price + exit_price)
                    # slippage = 10
                    final_points = points - slippage
                    # final_points = points
                    trade = {
                        "Index": index,
                        "Strike": strike,
                        "Option Type": asset_class,
                        "Expiry": expiry,
                        "Signal Generated At": signal_creation_time,
                        "Trade Type": "SELL",
                        "Entry Time": entry_time,
                        "Entry Price": entry_price,
                        "Initial SL": trade_initial_sl,
                        "Final SL": trade_final_sl,
                        "Exit Time": exit_time,
                        "Exit Price": exit_price,
                        "Points Captured": points,
                        "Slippages": slippage,
                        "After Costs": final_points,
                        "PnL": final_points * qty,
                        "Remarks": remark,
                        "Qty": qty,
                        # "Leverage": "5x",
                        "ROI%": (final_points * qty / PORTFOLIO_VALUE) * 100,
                        "Trade Year": entry_time.year,
                        "Trade Month": entry_time.month,
                    }
                    trade_book.append(trade)
                    points = 0
                    in_trade = False
                    already_signal_exists = False
                    remark = ""
                    is_trailing_active = False
                    eod_exit_flag = False

    trade_book_df = pd.DataFrame(trade_book)
    return trade_book_df

In [20]:
async def trade(df, signal_ma, trailing_ma, time_of_day):

    start_date = dt.date(2017, 1, 1)
    end_date = dt.date(2024, 6, 30)

    current_date = start_date

    combined_trades = pd.DataFrame()
    total_trades = pd.DataFrame()

    while current_date <= end_date:
        if current_date in trading_days_set:

            starting_time = dt.time(9, 15)
            # time_of_day = dt.time(9, 30)
            ending_time = dt.time(15, 30)

            search_datetime = dt.datetime.combine(current_date, time_of_day)

            spot_open = df.loc[df["datetime"] >= search_datetime, "open"].iloc[0]
            # print(spot_open)

            spot_atm = int(round(spot_open / 25) * 25)
            # print(spot_atm)

            nearest_expiry = await get_expiry_midcpnifty(current_date)
            # print(nearest_expiry)
    
            ce_df = await fetch_data(
                index=INDEX,
                start_date=current_date,
                start_time=starting_time,
                end_date=current_date,
                end_time=ending_time,
                strike=spot_atm,
                asset_class="C",
                expiry=nearest_expiry,
            )
            if not isinstance(ce_df, str) and (ce_df is not None):
                # print("IF CONDITION TRIGGERED -> CE Option")
                # ce_df = ce_df.rename(
                #     {"open": "o", "high": "h", "low": "l", "close": "c"}
                # )
                ce_df = ce_df.select(["datetime", "o", "h", "l", "c"])
                ce_df = resample(ce_df, "3m")
                ce_df_pandas = ce_df.to_pandas()
                ce_df = generate_signals2(ce_df_pandas, signal_ma, trailing_ma)
                # print(ce_df.tail())
            else:
                # print("ELSE CONDITION TRIGGERED -> CE Option")
                # print(ce_df)
                current_date += dt.timedelta(days=1)
                continue

            pe_df = await fetch_data(
                index=INDEX,
                start_date=current_date,
                start_time=starting_time,
                end_date=current_date,
                end_time=ending_time,
                strike=spot_atm,
                asset_class="P",
                expiry=nearest_expiry,
            )
            if not isinstance(ce_df, str) and pe_df is not None:
                # print("IF CONDITION TRIGGERED -> PE Option")
                # pe_df = pe_df.rename(
                #     {"open": "o", "high": "h", "low": "l", "close": "c"}
                # )
                pe_df = pe_df.select(["datetime", "o", "h", "l", "c"])
                pe_df = resample(pe_df, "3m")
                pe_df_pandas = pe_df.to_pandas()
                pe_df = generate_signals2(pe_df_pandas, signal_ma, trailing_ma)
                # print(pe_df.tail())
            else:
                # print("ELSE CONDITION TRIGGERED -> PE Option")
                # print(pe_df)
                current_date += dt.timedelta(days=1)
                continue

            # print(
            #     ce_df_pandas.to_string(), "\n", pe_df_pandas.to_string()
            # )

            # print('WORKING ON CE TRADES')
            ce_trades = await trade_mtrend_option_selling(
                df=ce_df_pandas,
                index=INDEX,
                strike=spot_atm,
                asset_class="C",
                expiry=nearest_expiry,
                search_datetime=search_datetime,
                # starting_index=starting_index,
            )
            # print('WORKING ON PE TRADES')
            pe_trades = await trade_mtrend_option_selling(
                df=pe_df_pandas,
                index=INDEX,
                strike=spot_atm,
                asset_class="P",
                expiry=nearest_expiry,
                search_datetime=search_datetime,
                # starting_index=starting_index,
            )
            combined_trades = pd.concat([combined_trades, ce_trades], ignore_index=True)
            combined_trades = pd.concat([combined_trades, pe_trades], ignore_index=True)
            # print(combined_trades)

        current_date += dt.timedelta(days=1)

    total_trades = pd.concat([total_trades, combined_trades], ignore_index=True)

    return total_trades

# tb = await trade(data)
# tb

In [21]:
def generate_stats(tb_expiry, signal_ma, trailing_ma, time_of_day):
    stats_df8 = pd.DataFrame(
        index=range(2017, 2025),
        columns=[
            "Total ROI",
            "Total Trades",
            "Win Rate",
            "Avg Profit% per Trade",
            "Avg Loss% per Trade",
            "Max Drawdown",
            "ROI/DD Ratio",
            "Variation",
        ],
    )
    combined_df_sorted = tb_expiry
    # combined_df_sorted = tb_expiry_ce
    # combined_df_sorted = tb_expiry_pe
    
    # Iterate over each year
    for year in range(2017, 2025):
        # Filter trades for the current year
        year_trades = combined_df_sorted[(combined_df_sorted["Trade Year"] == year)]
    
        # Calculate total ROI
        total_roi = year_trades["ROI%"].sum()
    
        # Calculate total number of trades
        total_trades = len(year_trades)
    
        # Calculate win rate
        win_rate = (year_trades["ROI%"] > 0).mean() * 100
    
        # Calculate average profit per trade
        avg_profit = year_trades[year_trades["ROI%"] > 0]["ROI%"].mean()
    
        # Calculate average loss per trade
        avg_loss = year_trades[year_trades["ROI%"] < 0]["ROI%"].mean()
    
        # Calculate maximum drawdown
        max_drawdown = (
            year_trades["ROI%"].cumsum() - year_trades["ROI%"].cumsum().cummax()
        ).min()
    
        # Calculate ROI/DD ratio
        roi_dd_ratio = total_roi / abs(max_drawdown)

        variation = f'{signal_ma} , {trailing_ma}, {time_of_day}'
    
        # Store the statistics in the DataFrame
        stats_df8.loc[year] = [
            total_roi,
            total_trades,
            win_rate,
            avg_profit,
            avg_loss,
            max_drawdown,
            roi_dd_ratio,
            variation,
        ]
    
    # Calculate overall statistics
    overall_total_roi = stats_df8["Total ROI"].sum()
    overall_total_trades = stats_df8["Total Trades"].sum()
    overall_win_rate = (combined_df_sorted["ROI%"] > 0).mean() * 100
    overall_avg_profit = combined_df_sorted[combined_df_sorted["ROI%"] > 0]["ROI%"].mean()
    overall_avg_loss = combined_df_sorted[combined_df_sorted["ROI%"] < 0]["ROI%"].mean()
    overall_max_drawdown = (
        combined_df_sorted["ROI%"].cumsum() - combined_df_sorted["ROI%"].cumsum().cummax()
    ).min()
    overall_roi_dd_ratio = overall_total_roi / abs(overall_max_drawdown)
    overall_variation = variation
    
    # Store the overall statistics in the DataFrame
    stats_df8.loc["Overall"] = [
        overall_total_roi,
        overall_total_trades,
        overall_win_rate,
        overall_avg_profit,
        overall_avg_loss,
        overall_max_drawdown,
        overall_roi_dd_ratio,
        overall_variation,
    ]
    return {overall_roi_dd_ratio: stats_df8}

In [22]:
# i = 10
# j = 4
# k = dt.time(9, 45)
# tb = await trade(data, i, j, k)

In [24]:
# stats_dict = {}
# tb_expiry = tb
# tb_ce = tb[tb['Option Type'] == 'C']
# tb_pe = tb[tb['Option Type'] == 'P']
# stats_expiry = generate_stats(tb_expiry, i, j, k)
# stats_ce = generate_stats(tb_ce, i, j, k)
# stats_pe = generate_stats(tb_pe, i, j, k)
# for overall_roi_dd_ratio, stats_df in stats_expiry.items():
#         if overall_roi_dd_ratio is not None and overall_roi_dd_ratio > 4:
#             stats_dict[overall_roi_dd_ratio] = stats_df
#             # Print the stats
#             print('Overall Stats Combined')
#             print(stats_df.to_string())

# for overall_roi_dd_ratio, stats_df in stats_ce.items():
#         if overall_roi_dd_ratio is not None and overall_roi_dd_ratio > 4:
#             stats_dict[overall_roi_dd_ratio] = stats_df
#             # Print the stats
#             print('Only CE')
#             print(stats_df.to_string())

# for overall_roi_dd_ratio, stats_df in stats_pe.items():
#         if overall_roi_dd_ratio is not None and overall_roi_dd_ratio > 4:
#             stats_dict[overall_roi_dd_ratio] = stats_df
#             # Print the stats
#             print('Only PE')
#             print(stats_df.to_string())

In [25]:
# tb['Expiry'] = pd.to_datetime(tb['Expiry'])
# tb['Entry Time'] = pd.to_datetime(tb['Entry Time'])
# tb['DTE'] = 1 + (tb['Expiry'] - tb['Entry Time']).dt.days

In [26]:
# tb

In [27]:
stats_dict = {}

times = [dt.time(12, 0), dt.time(12, 30), dt.time(13, 0), dt.time(13, 30), dt.time(14, 0), dt.time(14, 30)]
# times = [dt.time(12, 0)]
for i in range(5, 60, 5):
    for j in range(4, 11, 2):
        for k in times:
            print(f'Signal MA {i}, Trailing MA {j}, Time of Day {k}')
            tb = await trade(data, i, j, k)
            if not isinstance(tb, str):
                # print(tb)
                tb_expiry = tb
                tb_ce = tb[tb['Option Type'] == 'C']
                tb_pe = tb[tb['Option Type'] == 'P']
                stats_expiry = generate_stats(tb_expiry, i, j, k)
                stats_ce = generate_stats(tb_ce, i, j, k)
                stats_pe = generate_stats(tb_pe, i, j, k)
                for overall_roi_dd_ratio, stats_df in stats_expiry.items():
                        if overall_roi_dd_ratio is not None and overall_roi_dd_ratio > 4:
                            stats_dict[overall_roi_dd_ratio] = stats_df
                            # Print the stats
                            print('Overall Stats Combined')
                            print(stats_df.to_string())

                for overall_roi_dd_ratio, stats_df in stats_ce.items():
                        if overall_roi_dd_ratio is not None and overall_roi_dd_ratio > 4:
                            stats_dict[overall_roi_dd_ratio] = stats_df
                            # Print the stats
                            print('Only CE')
                            print(stats_df.to_string())

                for overall_roi_dd_ratio, stats_df in stats_pe.items():
                        if overall_roi_dd_ratio is not None and overall_roi_dd_ratio > 4:
                            stats_dict[overall_roi_dd_ratio] = stats_df
                            # Print the stats
                            print('Only PE')
                            print(stats_df.to_string())

sorted_stats = {k: v for k, v in sorted(stats_dict.items(), key=lambda item: item[0], reverse=True)}

Signal MA 5, Trailing MA 4, Time of Day 12:00:00


KeyError: 'Option Type'

In [ ]:
sorted_stats

In [80]:
tb["Entry Time"] = pd.to_datetime(tb["Entry Time"])
tb_expiry = tb[tb["Entry Time"].dt.date == tb["Expiry"]]
tb_calls = tb[tb['Option Type'] == 'C']
tb_puts = tb[tb['Option Type'] == 'P']
tb_expiry_ce = tb_expiry[tb_expiry['Option Type'] == 'C']
tb_expiry_pe = tb_expiry[tb_expiry['Option Type'] == 'P']
# tb['ROI%'].sum()

In [81]:
tb["ROI%"].sum() , tb_expiry_ce['ROI%'].sum() , tb_expiry_pe['ROI%'].sum()

(-99.78293370000004, 15.088490399999976, -114.8714241)

In [78]:
stats_df8 = pd.DataFrame(
    index=range(2017, 2025),
    columns=[
        "Total ROI",
        "Total Trades",
        "Win Rate",
        "Avg Profit% per Trade",
        "Avg Loss% per Trade",
        "Max Drawdown",
        "ROI/DD Ratio",
    ],
)
# combined_df_sorted = tb_expiry
combined_df_sorted = tb_expiry_ce
# combined_df_sorted = tb_expiry_pe

# Iterate over each year
for year in range(2017, 2025):
    # Filter trades for the current year
    year_trades = combined_df_sorted[(combined_df_sorted["Trade Year"] == year)]

    # Calculate total ROI
    total_roi = year_trades["ROI%"].sum()

    # Calculate total number of trades
    total_trades = len(year_trades)

    # Calculate win rate
    win_rate = (year_trades["ROI%"] > 0).mean() * 100

    # Calculate average profit per trade
    avg_profit = year_trades[year_trades["ROI%"] > 0]["ROI%"].mean()

    # Calculate average loss per trade
    avg_loss = year_trades[year_trades["ROI%"] < 0]["ROI%"].mean()

    # Calculate maximum drawdown
    max_drawdown = (
        year_trades["ROI%"].cumsum() - year_trades["ROI%"].cumsum().cummax()
    ).min()

    # Calculate ROI/DD ratio
    roi_dd_ratio = total_roi / abs(max_drawdown)

    # Store the statistics in the DataFrame
    stats_df8.loc[year] = [
        total_roi,
        total_trades,
        win_rate,
        avg_profit,
        avg_loss,
        max_drawdown,
        roi_dd_ratio,
    ]

# Calculate overall statistics
overall_total_roi = stats_df8["Total ROI"].sum()
overall_total_trades = stats_df8["Total Trades"].sum()
overall_win_rate = (combined_df_sorted["ROI%"] > 0).mean() * 100
overall_avg_profit = combined_df_sorted[combined_df_sorted["ROI%"] > 0]["ROI%"].mean()
overall_avg_loss = combined_df_sorted[combined_df_sorted["ROI%"] < 0]["ROI%"].mean()
overall_max_drawdown = (
    combined_df_sorted["ROI%"].cumsum() - combined_df_sorted["ROI%"].cumsum().cummax()
).min()
overall_roi_dd_ratio = overall_total_roi / abs(overall_max_drawdown)

# Store the overall statistics in the DataFrame
stats_df8.loc["Overall"] = [
    overall_total_roi,
    overall_total_trades,
    overall_win_rate,
    overall_avg_profit,
    overall_avg_loss,
    overall_max_drawdown,
    overall_roi_dd_ratio,
]
stats_df8

Total ROI Total Trades Win Rate Avg Profit% per Trade  \
2017       3.6250          264  32.1970                0.3644   
2018      19.1880          212  40.0943                0.5358   
2019       6.5628          246  33.7398                0.6118   
2020      -5.2716          246  33.3333                1.0822   
2021       9.6570          241  37.3444                0.6950   
2022      17.0889          267  38.5768                0.5368   
2023       2.3588          245  33.4694                0.4143   
2024      -7.4054           72  33.3333                0.2526   
Overall   45.8036    1793.0000  35.3597                0.5898   

        Avg Loss% per Trade Max Drawdown ROI/DD Ratio  
2017                -0.1528      -2.8217       1.2847  
2018                -0.2075      -4.9298       3.8923  
2019                -0.2712      -9.2831       0.7070  
2020                -0.5733     -24.2974      -0.2170  
2021                -0.3503      -7.3336       1.3168  
2022                -0.2329      -8.3163       2.0549  
2023                -0.1939      -9.8195       0.2402  
2024                -0.2806      -8.3529      -0.8866  
Overall             -0.2831     -31.4700       1.4555

In [77]:
tb_expiry

Index  Strike Option Type      Expiry Signal Generated At Trade Type  \
0      bnf   18000           C  2017-01-05 2017-01-05 11:30:00       SELL   
1      bnf   18000           C  2017-01-05 2017-01-05 11:42:00       SELL   
2      bnf   18000           P  2017-01-05 2017-01-05 11:15:00       SELL   
3      bnf   18000           P  2017-01-05 2017-01-05 12:33:00       SELL   
4      bnf   18900           C  2017-01-12 2017-01-12 11:27:00       SELL   
5      bnf   18900           C  2017-01-12 2017-01-12 12:48:00       SELL   
6      bnf   18900           C  2017-01-12 2017-01-12 13:24:00       SELL   
7      bnf   18900           C  2017-01-12 2017-01-12 13:30:00       SELL   
8      bnf   18900           P  2017-01-12 2017-01-12 11:15:00       SELL   
9      bnf   18900           P  2017-01-12 2017-01-12 12:00:00       SELL   
10     bnf   18900           P  2017-01-12 2017-01-12 12:36:00       SELL   
11     bnf   18900           P  2017-01-12 2017-01-12 13:36:00       SELL   
12     bnf   18900           P  2017-01-12 2017-01-12 14:03:00       SELL   
13     bnf   18900           P  2017-01-12 2017-01-12 14:18:00       SELL   
14     bnf   18900           P  2017-01-12 2017-01-12 14:27:00       SELL   
15     bnf   18900           P  2017-01-12 2017-01-12 15:24:00       SELL   
16     bnf   19100           C  2017-01-19 2017-01-19 11:24:00       SELL   
17     bnf   19100           C  2017-01-19 2017-01-19 11:33:00       SELL   
18     bnf   19100           C  2017-01-19 2017-01-19 13:21:00       SELL   
19     bnf   19100           C  2017-01-19 2017-01-19 13:36:00       SELL   
20     bnf   19100           C  2017-01-19 2017-01-19 13:51:00       SELL   
21     bnf   19100           C  2017-01-19 2017-01-19 14:48:00       SELL   
22     bnf   19100           P  2017-01-19 2017-01-19 11:18:00       SELL   
23     bnf   19100           P  2017-01-19 2017-01-19 13:06:00       SELL   
24     bnf   19100           P  2017-01-19 2017-01-19 13:57:00       SELL   
25     bnf   19100           P  2017-01-19 2017-01-19 14:15:00       SELL   
26     bnf   19100           P  2017-01-19 2017-01-19 15:24:00       SELL   
27     bnf   19200           C  2017-01-25 2017-01-25 11:18:00       SELL   
28     bnf   19200           C  2017-01-25 2017-01-25 11:27:00       SELL   
29     bnf   19200           C  2017-01-25 2017-01-25 11:45:00       SELL   
30     bnf   19200           P  2017-01-25 2017-01-25 11:18:00       SELL   
31     bnf   19200           P  2017-01-25 2017-01-25 11:42:00       SELL   
32     bnf   19200           P  2017-01-25 2017-01-25 11:51:00       SELL   
33     bnf   20000           C  2017-02-02 2017-02-02 11:15:00       SELL   
34     bnf   20000           C  2017-02-02 2017-02-02 12:27:00       SELL   
35     bnf   20000           C  2017-02-02 2017-02-02 12:33:00       SELL   
36     bnf   20000           C  2017-02-02 2017-02-02 12:45:00       SELL   
37     bnf   20000           C  2017-02-02 2017-02-02 12:57:00       SELL   
38     bnf   20000           C  2017-02-02 2017-02-02 13:12:00       SELL   
39     bnf   20000           P  2017-02-02 2017-02-02 11:21:00       SELL   
40     bnf   20000           P  2017-02-02 2017-02-02 12:54:00       SELL   
41     bnf   20400           C  2017-02-09 2017-02-09 11:18:00       SELL   
42     bnf   20400           C  2017-02-09 2017-02-09 11:24:00       SELL   
43     bnf   20400           C  2017-02-09 2017-02-09 11:42:00       SELL   
44     bnf   20400           C  2017-02-09 2017-02-09 11:57:00       SELL   
45     bnf   20400           C  2017-02-09 2017-02-09 12:03:00       SELL   
46     bnf   20400           C  2017-02-09 2017-02-09 12:27:00       SELL   
47     bnf   20400           C  2017-02-09 2017-02-09 13:18:00       SELL   
48     bnf   20400           C  2017-02-09 2017-02-09 13:33:00       SELL   
49     bnf   20400           C  2017-02-09 2017-02-09 13:45:00       SELL   
50     bnf   20400           P  2017-02-09 2017-02-09 12:48:00       SELL   
5